In [1]:
import pandas as pd
import folium
import numpy as np
from folium import plugins

In [2]:
raw_original=pd.read_csv("Motor_Vehicle_Collisions_-_Crashes.csv")

//anaconda3/lib/python3.7/site-packages/IPython/core/interactiveshell.py:3063: DtypeWarning: Columns (3) have mixed types.Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


In [3]:
crossData = raw_original[['CRASH DATE','CRASH TIME','LATITUDE','NUMBER OF PERSONS INJURED','NUMBER OF PERSONS KILLED','NUMBER OF PEDESTRIANS INJURED','NUMBER OF PEDESTRIANS KILLED','LONGITUDE','NUMBER OF MOTORIST INJURED','NUMBER OF MOTORIST KILLED','ON STREET NAME', 'CROSS STREET NAME']]
crossData=crossData[(crossData.LONGITUDE.isnull() == False) & ( crossData.LATITUDE.isnull()== False)]
crossInjured=crossData[['NUMBER OF PERSONS INJURED','LATITUDE','LONGITUDE','ON STREET NAME', 'CROSS STREET NAME']]
crossInjured=crossInjured.dropna(axis=0)

In [4]:
cList=[]
for x in range(0, len(crossInjured)):
    name=str(str(crossInjured['ON STREET NAME'].iloc[x])+', '+str(crossInjured['CROSS STREET NAME'].iloc[x]))
    cList.append(name)
crossInjured['Intersection']=cList

In [5]:
coordinates=crossInjured[['Intersection', 'LATITUDE', 'LONGITUDE']]
coordNoDup=coordinates.drop_duplicates(subset='Intersection')
crossCount=crossInjured.drop(labels=['ON STREET NAME', 'CROSS STREET NAME','LATITUDE', 'LONGITUDE'], axis=1)

In [6]:
#For calculating the sum of injured people
crossSum=crossCount.groupby('Intersection').sum()
merged=coordNoDup.merge(crossSum,how='inner', on='Intersection')
filtInjured=merged.sort_values(by='NUMBER OF PERSONS INJURED',axis=0, ascending=False).iloc[0:10]

In [7]:
#Total number of accidents
crossCount=crossCount.groupby('Intersection').count()
mergedAcc=coordNoDup.merge(crossCount,on='Intersection')
filtAcc=mergedAcc.sort_values(by='NUMBER OF PERSONS INJURED',axis=0, ascending=False).iloc[0:10]

In [8]:
#Number of persons killed
crossKilled=crossData[['NUMBER OF PERSONS KILLED','LATITUDE','LONGITUDE','ON STREET NAME', 'CROSS STREET NAME']]
crossKilled=crossKilled.dropna(axis=0)
crossKilled=crossKilled[crossKilled['NUMBER OF PERSONS KILLED']>0.0]

In [9]:
cList=[]
for x in range(0, len(crossKilled)):
    name=str(str(crossKilled['ON STREET NAME'].iloc[x])+', '+str(crossKilled['CROSS STREET NAME'].iloc[x]))
    cList.append(name)
crossKilled['Intersection']=cList

In [10]:
coordinatesKilled=crossKilled[['Intersection', 'LATITUDE', 'LONGITUDE']]
coordNoDupK=coordinatesKilled.drop_duplicates(subset='Intersection')
crossK=crossKilled.drop(labels=['ON STREET NAME', 'CROSS STREET NAME','LATITUDE', 'LONGITUDE'], axis=1)
crossSumK=crossK.groupby('Intersection').sum()
mergedK=coordNoDup.merge(crossSumK,how='inner', on='Intersection')
filtK=mergedK.sort_values(by='NUMBER OF PERSONS KILLED',axis=0, ascending=False).iloc[0:10]

In [11]:
#TOP THEN INTERSECTIONS FOR ACCIDENTS, KILLED, INJURED
map_hooray = folium.Map(location=[40.730610, -73.935242],
                    zoom_start = 11)

folium.TileLayer('Stamen Toner').add_to(map_hooray)

#fg = folium.FeatureGroup(name='All groups')
#map_hooray.add_child(fg)

#g1 = plugins.FeatureGroupSubGroup(fg,name='Top ten accidents')
g1 = folium.FeatureGroup(name='Top ten accidents')
map_hooray.add_child(g1)

#g2 = plugins.FeatureGroupSubGroup(fg,name='Top ten persons killed')
g2 = folium.FeatureGroup(name='Top ten persons killed')
map_hooray.add_child(g2)

#g3 = plugins.FeatureGroupSubGroup(fg,name='Top ten persons injured')
g3 = folium.FeatureGroup(name='Top ten persons injured')
map_hooray.add_child(g3)

sumK=filtK['NUMBER OF PERSONS KILLED'].sum(axis=0)
for x in range(0,len(filtK)):
    percentage=filtK['NUMBER OF PERSONS KILLED'].iloc[x]/sumK
    percentage=np.log10(filtK['NUMBER OF PERSONS KILLED'].iloc[x])/np.log10(sumK)
    
    
    text=str('Number of killed: '+str(filtK['NUMBER OF PERSONS KILLED'].iloc[x]))
    folium.CircleMarker([filtK.LATITUDE.iloc[x], filtK.LONGITUDE.iloc[x]],
                        radius=15*percentage,
                        popup=text,
                        color='red', fill=True, opacity=0.3+percentage
                        ).add_to(g2)


sumA=filtAcc['NUMBER OF PERSONS INJURED'].sum(axis=0)
for x in range(0,len(filtAcc)):
    
    #percentage=filtAcc['NUMBER OF PERSONS INJURED'].iloc[x]/sumA
    percentage=np.log10(filtAcc['NUMBER OF PERSONS INJURED'].iloc[x])/np.log10(sumA)


    
    text=str('Number of accidents: '+str(filtAcc['NUMBER OF PERSONS INJURED'].iloc[x]))
    folium.CircleMarker([filtAcc.LATITUDE.iloc[x], filtAcc.LONGITUDE.iloc[x]],
                        radius=15*percentage,
                        popup=text,
                        color='blue',fill=True, opacity=0.3+percentage
                        ).add_to(g1)

sumJ=filtInjured['NUMBER OF PERSONS INJURED'].sum(axis=0)
for x in range(0,len(filtInjured)):
    #percentage=filtAcc['NUMBER OF PERSONS INJURED'].iloc[x]/sumJ
    percentage=np.log10(filtAcc['NUMBER OF PERSONS INJURED'].iloc[x])/np.log10(sumJ)
    
    text=str('Number of injured: '+str(filtInjured['NUMBER OF PERSONS INJURED'].iloc[x]))
    folium.CircleMarker([filtInjured.LATITUDE.iloc[x], filtInjured.LONGITUDE.iloc[x]],
                        radius=15*percentage,
                        popup=text,
                        color='yellow',fill=True, opacity=0.3+percentage
                        ).add_to(g3)

folium.LayerControl(collapsed=False).add_to(map_hooray)


#map_hooray.save('mapv1.html')
map_hooray # Calls the map to display

In [12]:
#VEHICLE TYPES
typeData=raw_original[['CRASH DATE','LATITUDE','LONGITUDE', 'VEHICLE TYPE CODE 1','CONTRIBUTING FACTOR VEHICLE 1','ON STREET NAME', 'CROSS STREET NAME']]
typeData=typeData[(typeData.LONGITUDE.isnull() == False) & ( typeData.LATITUDE.isnull()== False)]
typeData=typeData.dropna(axis=0)

oneCar=typeData[['VEHICLE TYPE CODE 1','CRASH DATE']]
oneCar=oneCar.groupby('VEHICLE TYPE CODE 1').count()
toptenCar=oneCar.sort_values(by='CRASH DATE',axis=0, ascending=False).iloc[0:10]
namesCar=list(toptenCar.index)


In [13]:
sport=typeData[typeData['VEHICLE TYPE CODE 1']=='SPORT UTILITY / STATION WAGON']
sedan=typeData[typeData['VEHICLE TYPE CODE 1']=='Sedan']
taxi=typeData[typeData['VEHICLE TYPE CODE 1']=='TAXI']
bus=typeData[typeData['VEHICLE TYPE CODE 1']=='BUS']
sport2=typeData[typeData['VEHICLE TYPE CODE 1']=='Station Wagon/Sport Utility Vehicle']
van=typeData[typeData['VEHICLE TYPE CODE 1']=='VAN']
pickup=typeData[typeData['VEHICLE TYPE CODE 1']=='PICK-UP TRUCK']
bus=typeData[typeData['VEHICLE TYPE CODE 1'] == 'BUS']
pickup=typeData[typeData['VEHICLE TYPE CODE 1'] == 'PICK-UP TRUCK']

In [16]:
sport_combined=pd.concat([sport.sample(500),sport2.sample(500)], axis=0)
carList=[sport_combined,sedan.sample(1000),taxi.sample(1000),van.sample(1000), pickup.sample(1000),bus.sample(1000)]

In [17]:
m = folium.Map(location=[40.730610, -73.935242],
                    zoom_start = 11)

g1 = folium.FeatureGroup(name='SPORT UTILITY / STATION WAGON')
m.add_child(g1)

g2 = folium.FeatureGroup(name='Sedan')
m.add_child(g2)

g3 = folium.FeatureGroup(name='TAXI')
m.add_child(g3)

g4 = folium.FeatureGroup(name='VAN')
m.add_child(g4)

g5 = folium.FeatureGroup(name='PICK UP TRUCK')
m.add_child(g5)

g6 = folium.FeatureGroup(name='BUS')
m.add_child(g6)

group_list=[g1,g2,g3,g4,g5,g6]

folium.TileLayer('Stamen Toner').add_to(m)
colors=['brown','red','blue','green','orange','black']


count=0;''
for car in carList:
    for x in range(0,len(car)):
        folium.CircleMarker([car.LATITUDE.iloc[x],car.LONGITUDE.iloc[x]],
                        radius=2,
                        popup=car['VEHICLE TYPE CODE 1'].iloc[x],
                        color=colors[count],fill=True, opacity=0.4
                        ).add_to(group_list[count])
    count +=1
folium.LayerControl(collapsed=False).add_to(m)
m